28/Enero/2025

Obtener los DENUES de Mazatlán en la zona de estudio 

Basado en el KMZ llamado Manzanas_Pinsa se exporto con google earth pro en formato KML, una vez con ese formato se accedio a la siguiente liga: https://mygeodata.cloud/conversion#result que converitie el KML a un formato CSV, para obtener los AGEB y filtrar los DENUES en las Zonas Necesarias


Se descargo la base de datos del DENUE para conocer las unidades economicas en la zona de interes rasultados de la consulta en 2024 con fecha de descarga del 28/Enero/2025 liga: https://www.inegi.org.mx/app/mapa/denue/default.aspx


Se descargo la base de datos del AGEB para sinaloa para concer más sobre la zona de estudio, base de datos del 2020 con fecha de descarga del 28/Enero/2025 liga: https://www.inegi.org.mx/app/scitel/Default?ev=10

Se descargo el diccionario de la base de datos del SCIAN. Fecha de consulta 30/Enero/2025 en la liga https://www.inegi.org.mx/scian/#


In [1]:
import sys
import pandas as pd
import numpy as np
#import plotly.express as px 

sys.path.append('../Funciones')  # Aacceder a la carpeta Funciones

from funciones import calcular_distancia_haversine
from funciones import graficar_interactivo
from funciones import analizar_columnas

ModuleNotFoundError: No module named 'matplotlib'

In [3]:
# Cargar las bases de datos
denue_m = pd.read_csv("INEGI_DENUE_28012025.csv", encoding='ISO-8859-1') # INEGI DENUE
#ageb_sina = pd.read_csv("RESAGEBURB_25CSV20.csv") # Base de datos de AGEB 
extendido = pd.read_excel("Extendido.xlsx") # Zona extendida
nuclear = pd.read_excel("Nuclear.xlsx") # Zona Nuclear
scian = pd.read_excel("C:/Users/julio/OneDrive/Documentos/Ideas Frescas/MacroDatos/Diccionarios/Diccionario SCIAN.xlsx") # Base de datos diccinario del SCIAN


# Filtrar por AGEB y Manzana 
zona_total_estudio= pd.concat([extendido,nuclear], ignore_index=True) # Concatenamos los dos Dataframes
zona_total_estudio = zona_total_estudio[["CVE_AGEB","CVE_MZA"]] # Solo utilizamos las variables para los filtros


# Diccionario de datos de la base de datos SCIAN, 
scian = scian[scian["Código"].astype(str).str.fullmatch(r"^\d{3}")] # Se filtro solo a los codigos de 3 digitos que nos indican la principal actividad economico
scian["Título"] = scian["Título"] .str.rstrip("T") # Se limpia los datos de la Columna Título
scian = scian[["Código", "Título"]] # Solo usas las siguentes columnas para hacer el filtro 


# Filtras considenrando solo los AGEB que entran en la zona de estudio
zona_estudio_poligonos = list(set(extendido["CVE_AGEB"].unique()) | set(nuclear["CVE_AGEB"].unique())) # Obtener los valores únicos de ambas columnas y combinarlos en una sola lista


zona_estudio_poligonos = [str(x) for x in zona_estudio_poligonos] # Convertir todos los elementos de la lista a cadenas de texto (str)

#zona_estudio_poligonos

Analizis DENUES y la descripcion poblacional en las zonas de estudio trazadas en los poligonos de zona extendida y zona nuclear

In [4]:
# Diccionario de Variables 
'''
Diccionario de Columnas a Utilizar 
Nombre de la Unidad Económica: Es el nombre comercial o nombre exterior con el que se identifica o anuncia la unidad económica.

Código de la clase de actividad SCIAN: El código está asignado con base en la actividad principal que desarrolla la unidad económica y de acuerdo con el Sistema de Clasificación
Industrial para América del Norte.

Descripcion estrato personal ocupado: Permite identificar el tamaño de Unidades Económicas por el número
de personal que emplean.

Tipo de vialidad: Es la superficie del terreno destinada para el tránsito vehicular y/o peatonal, en la cual se encuentra ubicada la unidad económica (calle, avenida,
andado.

Tipo de asentamiento humano: Es la clasificación que se da al asentamiento humano de acuerdo con su función (colonia, fraccionamiento, unidad habitacional, etc.).

Nombre de asentamiento humano:Es el sustantivo propio con el cual se identifica el asentamiento humano.

Tipo centro comercial: Son los caracteres alfanuméricos con los que se identifica el tipo de plaza, centro comercial, mercado.

Tipo de establecimiento: En este tipo de establecimiento están comprendidas las viviendas cuando en algún espacio de la casa-habitación, que también está destinado a
otras actividades cotidianas, se realiza alguna actividad económica.

Fecha de incorporación al DENUE: Fecha en la que la unidad económica se integró al Directorio Estadístico Nacional de Unidades Económicas.

Área geoestadística básica: Marco Geoestadístico Naciona.

Manzana: xtensión territorial que está constituida por un grupo de
viviendas, edificios, predios, lotes o terrenos de uso habitacional, comercial, industrial o de servicios.

Latitud: Es la distancia que existe entre la unidad económica y el ecuador. 

Fecha en la que la unidad económica se integró al Directorio Estadístico Nacional de Unidades Económicas.

Longitud: Es la distancia que existe entre la unidad económica y el meridiano de Greenwich.-

'''

# Lista de variables a considerar y filtrado por esas columnas 
denue_m_poligonos = denue_m[[
 'Nombre de la Unidad Económica',
 'Código de la clase de actividad SCIAN',
 'Descripcion estrato personal ocupado',
 'Tipo de vialidad',
 'Tipo de asentamiento humano',
 'Nombre de asentamiento humano',
 'Tipo centro comercial',
 'Tipo de establecimiento',
 'Fecha de incorporación al DENUE',
 'Área geoestadística básica ',
 'Manzana',
 'Latitud',
 'Longitud' 
]]

#Base de datos de DENUE filtrado por el AGEB y Manzanas por los poligonos trazados para el area de estudio para conocer la zona. 
denue_m_poligonos = denue_m_poligonos.merge(zona_total_estudio,left_on=["Área geoestadística básica ", "Manzana"],right_on=["CVE_AGEB","CVE_MZA"]).replace({'*': '0', np.nan: "DESCONOCIDO"})

# Filtramos solo por los AGEB de estudio y limpiamos la base de datos
#denue_m_poligonos = denue_m_poligonos[denue_m_poligonos["Área geoestadística básica "].isin(zona_estudio_poligonos)].replace({'*': '0', np.nan: "Desconocido"})

# Limpieza de datos
# Solo se considerará el año en la Fecha de incorporación al DENU
denue_m_poligonos["Fecha de incorporación DENU"] = denue_m_poligonos["Fecha de incorporación al DENUE"].astype(str).str[:4]
# Posicionar la nueva columna en donde sea más facil leer la información 
col_f = denue_m_poligonos.pop("Fecha de incorporación DENU")
denue_m_poligonos.insert(9,"Fecha de incorporación DENU", col_f)

# Agregar la principal actividad economica SCIAN a cada DENUE, basado en el diccionario que se descargo 

# Considerar solo los tres primeros digitos  del SCIAN para hacer la conección con las dos bases de datos. 
denue_m_poligonos["CLAVE SCIAN"] = denue_m_poligonos["Código de la clase de actividad SCIAN"].astype(str).str[:3]

# Se unen las dos bases de datos para obtener la principal actividad economica
denue_m_poligonos = denue_m_poligonos.merge(scian,left_on="CLAVE SCIAN", right_on="Código", how = "left")

# Se renombra la columna a utilizar
denue_m_poligonos = denue_m_poligonos.rename(columns={"Título": "Principal Actividad Economica"})

# Se eliminan las columnas que ya no son necesarias 
denue_m_poligonos = denue_m_poligonos.drop(columns=["CLAVE SCIAN","Código","Fecha de incorporación al DENUE"])

# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = denue_m_poligonos.pop("Principal Actividad Economica")
denue_m_poligonos.insert(2,"Principal Actividad Economica", col_a)

# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = denue_m_poligonos.pop("Principal Actividad Economica")
denue_m_poligonos.insert(2,"Principal Actividad Economica", col_a)

In [5]:
# Crear el CSV de la base de datos filtrados 
#denue_m_poligonos.to_csv("DENUE_Mazatlan_Zona_poligonos.csv", index=False, encoding='ISO-8859-1')

In [6]:
denue_m_poligonos.head(3)

Nombre de la Unidad Económica  \
0                      ALMACENES CONGELADOS   
1                           CAMARONES VIVOS   
2  COMERCIALIZADORA DE MARISCOS MARIA ELISA   

   Código de la clase de actividad SCIAN   Principal Actividad Economica  \
0                                 114111           Pesca, caza y captura   
1                                 112513  Cría y explotación de animales   
2                                 114111           Pesca, caza y captura   

  Descripcion estrato personal ocupado Tipo de vialidad  \
0                     11 a 30 personas            CALLE   
1                       0 a 5 personas          AVENIDA   
2                     11 a 30 personas            CALLE   

  Tipo de asentamiento humano Nombre de asentamiento humano  \
0           PARQUE INDUSTRIAL              ALFREDO V BONFIL   
1                     COLONIA                EMILIO BARAGAN   
2           PARQUE INDUSTRIAL             ALFREDO V. BONFIL   

  Tipo centro comercial Tipo de establecimiento Fecha de incorporación DENU  \
0     PARQUE INDUSTRIAL                    Fijo                        2010   
1           DESCONOCIDO                    Fijo                        2024   
2     PARQUE INDUSTRIAL                    Fijo                        2013   

  Área geoestadística básica   Manzana    Latitud    Longitud CVE_AGEB  \
0                        1669       10  23.214153 -106.392982     1669   
1                        0374       38  23.203081 -106.412283     0374   
2                        1669        3  23.214409 -106.398566     1669   

   CVE_MZA  
0       10  
1       38  
2        3

In [7]:
df_actividades = denue_m_poligonos["Código de la clase de actividad SCIAN"].value_counts().reset_index()
df_actividades.columns = ["Código de la clase de actividad SCIAN", "Cantidad"]
df_actividades

Código de la clase de actividad SCIAN  Cantidad
0                                   461110       134
1                                   812110        72
2                                   722514        43
3                                   114111        42
4                                   722513        29
..                                     ...       ...
266                                 238290         1
267                                 221123         1
268                                 114112         1
269                                 112513         1
270                                 931310         1

[271 rows x 2 columns]

In [8]:
# Crear el CSV de la base de datos filtrados 
df_actividades.to_csv("DENUE_Mazatlan_Zona_poligonos_CLAVE.csv", index=False, encoding='ISO-8859-1')

In [ ]:
actividad_economi= analizar_columnas(denue_m_poligonos,"Principal Actividad Economica",60)
actividad_economi

In [ ]:
# Crear el CSV de la base de datos filtrados 
#actividad_economi.to_csv("Principal actividad economica en la zona.csv", index=False, encoding='ISO-8859-1')

In [ ]:
graficar_interactivo(denue_m_poligonos,'Descripcion estrato personal ocupado',"Número de empleados","Número de empleados en la zona poligonal.html",tipo_grafica='bar')

In [ ]:
# Calculareos en donde se centra la mayoria de las personas en la zona de estuido 

# Calculamos el número de DENUES que tiene de 0 a 5 personas empleadas hasta los 251 y más
personal_ocupado_dataframe = denue_m_poligonos["Descripcion estrato personal ocupado"].value_counts().reset_index()

# Pasamos los reultados a un DataFrame
personal_ocupado_dataframe.columns = ["Descripcion estrato personal ocupado", 'Cantidad']

# Promediamos el númerp de personas empleadas por tamaño del DENUE
datos = [2.5,8,20.5,75.5,40.5,251,175.5]

# Calculamos la cantida de personas por tamaño de DENUE
personal_ocupado_dataframe["Número de personas"] = personal_ocupado_dataframe["Cantidad"] * datos

# Calculamos el total de personas empleadas en la zona 
suma_ocupa = personal_ocupado_dataframe["Número de personas"].sum()

# Agregar la columna de porcentaje
personal_ocupado_dataframe["Porcentaje"] = (personal_ocupado_dataframe["Número de personas"] / suma_ocupa) * 100

# Ordenemos de Mayor a menor 
personal_ocupado_dataframe = personal_ocupado_dataframe.sort_values(by='Porcentaje', ascending=False)

# Agregar la columna de porcentaje acumulado
personal_ocupado_dataframe["Porcentaje Acumulado"] = personal_ocupado_dataframe["Porcentaje"].cumsum()


porcentaje = 100
# Filtrar solo los valores cuyo porcentaje acumulado es menor o igual al especificado
personal_ocupado_dataframe = personal_ocupado_dataframe[personal_ocupado_dataframe["Porcentaje Acumulado"] <= porcentaje]
    

print(f"El número de personas flotantes que se considera como trafico de personas en la zona de estudio es de: '{suma_ocupa}'. Los datos mostrados muetran el tamaño de las empresas que ocupan en {porcentaje} de todo el trafico de personas flotantes ")

personal_ocupado_dataframe

In [ ]:
# Crear el CSV de la base de datos filtrados 
#personal_ocupado_dataframe.to_csv("Descripcion estrato personal ocupado en la zona de estudio.csv", index=False, encoding='ISO-8859-1')

In [ ]:
# Filtarar los datos analizar dados por el resultado anterior 
list_personla_ocupado=personal_ocupado_dataframe["Descripcion estrato personal ocupado"].unique().tolist()

suma_personas=personal_ocupado_dataframe["Número de personas"].sum()

# Filtrar usando el método isin() para varios valores, donde se central el 60% de poblacion empleada 
df_filtrado = denue_m_poligonos[denue_m_poligonos["Descripcion estrato personal ocupado"].isin(list_personla_ocupado)]

print(f"El: {porcentaje}% de las personas empleadas da un total de {suma_personas}. Que se encuentran en las siguientes Colonias")

# Analizar las colonias donde se centra la mayoria de la población empleada
df_filtrado = analizar_columnas(df_filtrado,"Nombre de asentamiento humano",100)

suma_ocupa_2 = df_filtrado["Cantidad"].sum()

# Agregar la columna de porcentaje
df_filtrado["Porcentaje"] = (df_filtrado["Cantidad"] / suma_ocupa_2) * 100

# Ordenemos de Mayor a menor 
df_filtrado = df_filtrado.sort_values(by='Porcentaje', ascending=False)

# Agregar la columna de porcentaje acumulado
df_filtrado["Porcentaje Acumulado"] = df_filtrado["Porcentaje"].cumsum()

porcentaje_3 = 80
# Filtrar solo los valores cuyo porcentaje acumulado es menor o igual al especificado
df_filtrado = df_filtrado[df_filtrado["Porcentaje Acumulado"] <= porcentaje_3]
df_filtrado

In [ ]:
# Crear el CSV de la base de datos filtrados 
#df_filtrado.to_csv("Colonias donde se concentran el 80 porciento de los empleados.csv", index=False, encoding='ISO-8859-1')

In [ ]:
# Analizar las actividades en el parque Bonfil 
parque_bonfil = denue_m_poligonos[denue_m_poligonos["Nombre de asentamiento humano"] == "PARQUE INDUSTRIAL BONFIL"]
analizar_columnas(parque_bonfil,"Principal Actividad Economica",100)


In [ ]:
parque_bonfil["Principal Actividad Economica"].count()

In [ ]:
parque_bonfil["Descripcion estrato personal ocupado"].value_counts()

In [ ]:
#Analizar las empresas con mayor a 50 empleados 
lista_clientes_potenciales = ["51 a 100 personas","101 a 250 personas","251 y más personas"]
empresas_grandes=denue_m_poligonos[denue_m_poligonos["Descripcion estrato personal ocupado"].isin(lista_clientes_potenciales)]
# Empresas con más de 251 empleados o más 
total_empresas = empresas_grandes[["Nombre de la Unidad Económica"]].count().values[0]

print(f"En la zona hay un total de: {total_empresas} empresas, clientes potenciales para las bodegas.")
#empresas_grandes["Nombre de la Unidad Económica"].unique().tolist()

In [ ]:
# Colonias donde se encuentran ubicadas 
asenta_humano = empresas_grandes["Nombre de asentamiento humano"].value_counts().reset_index()

# Pasamos los reultados a un DataFrame
asenta_humano.columns = ["Nombre de asentamiento humano", 'Cantidad']
asenta_humano

In [ ]:
# Crear el CSV de la base de datos filtrados 
#asenta_humano.to_csv("Colonia donde se ubican clientes potenciales bodegas.csv", index=False, encoding='ISO-8859-1')

In [ ]:
# Ubicación exacta 
empresas_grandes = empresas_grandes[["Nombre de la Unidad Económica","Latitud","Longitud"]]
empresas_grandes

In [ ]:
# Crear el CSV de la base de datos filtrados 
#empresas_grandes.to_csv("Clientes potenciales bodegas.csv", index=False, encoding='ISO-8859-1')

In [ ]:
#Descripcion de las columnas 
'''
NOM_MUN: Municipio
AGEB: AGEB 
MZA: Manzanas que abarca por AGEB
POBTOT: Población Total
VIVTOT: Viviendas totales 
TVIVHAB: Total de vivienda Habitadas
VPH_AUTOM: Viviendas con Automovil
VPH_MOTO: Viviendas con Moto
'''

ageb_sina_filtrado_poligonal = (
    ageb_sina[(ageb_sina["NOM_MUN"] == "Mazatlán") & (ageb_sina["NOM_LOC"] == "Mazatlán")] # Selección de Municipio y localidad
    .loc[:, ["AGEB", "MZA", "POBTOT", "VIVTOT", "TVIVHAB", "VPH_AUTOM", "VPH_MOTO"]]  # Selección de columnas
    .replace({'*': '0', np.nan: 0})) #Remplazar los * y faltantes por 0

# Convertir varias columnas a numérico 
columns_to_convert = ['TVIVHAB', 'VPH_AUTOM', 'VPH_MOTO']
ageb_sina_filtrado_poligonal[columns_to_convert] = ageb_sina_filtrado_poligonal[columns_to_convert].apply(pd.to_numeric)

#Base de datos de AGEB filtrado por los poligonos trazados para el area de estudio para conocer la zona. 
ageb_sina_filtrado_poligonal = ageb_sina_filtrado_poligonal.merge(zona_total_estudio,left_on=["AGEB", "MZA"],right_on=["CVE_AGEB","CVE_MZA"])

# Agrupar por 'AGEB' y sumar los valores
ageb_sina_filtrado_poligonal = ageb_sina_filtrado_poligonal.groupby('AGEB', as_index=False).sum()

#Base de datos de AGEB filtrado por los poligonos trazados para el area de estudio para conocer la zona. 
#ageb_sina_filtrado_poligonal = ageb_sina_filtrado_poligonal[ageb_sina_filtrado_poligonal["AGEB"].isin(zona_estudio_poligonos)]

# Lista de columnas a sumar
columnas = ["POBTOT", "VIVTOT", "TVIVHAB", "VPH_AUTOM", "VPH_MOTO"]

# Diccionario con el nombre de la columna como clave y la suma como valor
resultados = {columna: ageb_sina_filtrado_poligonal[columna].sum().item() for columna in columnas}

#  DataFrame
AGEB_resultados_2020 = pd.DataFrame([resultados])

AGEB_resultados_2020


In [ ]:
# Obtener la lista de actividades económicas únicas
list_act = actividad_economi["Principal Actividad Economica"].unique().tolist()

actividad_evaluar = 1


In [ ]:
graficar_interactivo(actividad_economi,'Principal Actividad Economica',"Principal Actividad Economica","Principal Actividad Economica.html",tipo_grafica='pie')

In [ ]:
graficar_interactivo(denue_m_poligonos,'Tipo de asentamiento humano',"Tipo de asentamiento humano","Tipo de asentamiento humano.html",tipo_grafica='bar')

In [ ]:
graficar_interactivo(denue_m_poligonos,'Tipo de vialidad',"Tipo de vialidad","Tipo de vialidad.html",tipo_grafica='bar')

In [ ]:
graficar_interactivo(denue_m_poligonos,'Tipo centro comercial',"Tipos centro comercial","Tipos centro comercial zona poligonal.html",tipo_grafica='bar')

Analizis DENUES y la descripcion poblacional en las zonas de estudio en un radio de 2km alrededor del terreno.

In [ ]:
# Coordenadas de la zona de interés
coordenadas_zona_interes = [23.210198064478774, -106.40867487654303]

# Filtrar las filas dentro del radio de 2 km
denue_m['Distancia'] = denue_m.apply(lambda row: calcular_distancia_haversine(coordenadas_zona_interes[0], coordenadas_zona_interes[1], row['Latitud'], row['Longitud']), axis=1)

# Filtrar solo las filas dentro de 3 km
denue_m_filtrado = denue_m[denue_m['Distancia'] <= 3]

# Filtrar solo las columnas que nos importan
denue_m_clasificado=denue_m_filtrado[["Nombre de la Unidad Económica","Código de la clase de actividad SCIAN","Descripcion estrato personal ocupado","Tipo centro comercial","Corredor industrial, centro comercial o mercado público","Área geoestadística básica ","Latitud","Longitud","Fecha de incorporación al DENUE"]]

In [ ]:
# Crear el CSV de la base de datos filtrados 
#denue_m_clasificado.to_csv("DENUE_Filtrado_Mazatlan.csv", index=False, encoding='ISO-8859-1')

In [ ]:
graficar_comercio_interactivo(denue_m_clasificado,'Tipo centro comercial',"Tipos centro comercial","Tipos centro comercial.html",tipo_grafica='bar')

In [ ]:
graficar_comercio_interactivo(denue_m_clasificado,'Descripcion estrato personal ocupado',"Número de empleados","Número de empleados en la zona.html",tipo_grafica='bar')

In [ ]:
#Descripcion de las columnas 
'''
NOM_MUN: Municipio
AGEB: AGEB 
MZA: Manzanas que abarca por AGEB
POBTOT: Población Total
VIVTOT: Viviendas totales 
TVIVHAB: Total de vivienda Habitadas
VPH_AUTOM: Viviendas con Automovil
VPH_MOTO: Viviendas con Moto
'''

ageb_sina_filtrado = (
    ageb_sina[(ageb_sina["NOM_MUN"] == "Mazatlán") & (ageb_sina["NOM_LOC"] == "Mazatlán")] # Selección de Municipio y localidad
    .loc[:, ["AGEB", "MZA", "POBTOT", "VIVTOT", "TVIVHAB", "VPH_AUTOM", "VPH_MOTO"]]  # Selección de columnas
    .replace({'*': '0', np.nan: 0})) #Remplazar los * y faltantes por 0

# Convertir varias columnas a numérico 
columns_to_convert = ['TVIVHAB', 'VPH_AUTOM', 'VPH_MOTO']
ageb_sina_filtrado[columns_to_convert] = ageb_sina_filtrado[columns_to_convert].apply(pd.to_numeric)

# Agrupar por 'AGEB' y sumar los valores
ageb_sina_filtrado = ageb_sina_filtrado.groupby('AGEB', as_index=False).sum()

#Base de datos de AGEB filtrado en un radio de 2km del area de estudio para conocer la zona. 
AGEB_radio_2km=denue_m_clasificado["Área geoestadística básica "].unique().tolist()
ageb_sina_filtrado = ageb_sina_filtrado[ageb_sina_filtrado["AGEB"].isin(AGEB_radio_2km)]

# Lista de columnas a sumar
columnas = ["POBTOT", "VIVTOT", "TVIVHAB", "VPH_AUTOM", "VPH_MOTO"]

# Diccionario con el nombre de la columna como clave y la suma como valor
resultados = {columna: ageb_sina_filtrado[columna].sum().item() for columna in columnas}

#  DataFrame
AGEB_resultados_2020 = pd.DataFrame([resultados])

AGEB_resultados_2020

